# Spoofed Speech Detection via Maximum Likelihood Estimation of Gaussian Mixture Models
The goal of synthetic speech detection is to determine whether a speech segment $S$ is natural or synthetic/converted speeach.

This notebook implements a Gaussian mixture model maximum likelihood (GMM-ML) classifier for synthetic (spoofed) speech detection. This approach uses regular mel frequency cepstral coefficients (MFCC) features and gives the best performance on the [ASVspoof 2015 dataset](https://www.idiap.ch/dataset/avspoof) among the standard classifiers (GMM-SV, GMM-UBM, ...). For more background information see: *Hanilçi, Cemal, Tomi Kinnunen, Md Sahidullah, and Aleksandr Sizov. "Classifiers for synthetic speech detection: a comparison." In INTERSPEECH 2015*. The scripts use the Python package [Bob.Bio.SPEAR 2.04](https://pypi.python.org/pypi/bob.bio.spear/2.0.4) for speaker recogntion.

This work is part of the ["DDoS Resilient Emergency Dispatch Center"](https://www.dhs.gov/science-and-technology/news/2015/09/04/dhs-st-awards-university-houston-26m-cyber-security-research) project at the University of Houston, funded by the Department of Homeland Security (DHS).


April 19, 2015

Lorenzo Rossi

(lorenzo **[dot]** rossi **[at]** gmail **[dot]** com)

In [22]:
import os
import time
import numpy as np
import pandas as pd
import scipy
import cqcc_ext
import cfcc_ext
from bob.bio.spear import preprocessor, extractor
from bob.bio.gmm import algorithm
from bob.io.base import HDF5File
from bob.learn import em
from sklearn.metrics import classification_report, roc_curve, roc_auc_score

pd.set_option('display.max_rows', 300)

WAV_FOLDER = '/home/wujunting/data/ASVspoof2019/LA/' #'ASV2019dataset/wav/' # Path to folder containing speakers .wav subfolders
LABEL_FOLDER = '/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_cm_protocols/' #'ASV2019dataset/CM_protocol/' # Path to ground truth csv files

evalu_before = 'ASVspoof2019_LA_eval'
train_before = 'ASVspoof2019_LA_train'

EXT = '.wav'
%matplotlib inline

## Loading the Ground Truth
Load the dataframes (tables) with the labels for the training, development and evaluation (hold out) sets. Each subfolder corresponds to a different speaker. For example, T1 and D4 indicate the subfolders associated to the utterances and spoofed segments of speakers T1 and D4, respectively in training and development sets. Note that number of evaluation samples >> number of development samples >> testing samples.

You can either select the speakers in each set one by one, *e.g.*:
```
train_subfls = ['T1', 'T2']
``` 
will only load segments from speakers T1 and T2 for training,

or use all the available speakers in a certain subset by leaving the list empty, *e.g.*:
```
devel_subfls = [] 
```
will load all the available Dx speaker segments for the development stage. If you are running this notebook for the first time, you may want to start only with 2 or so speakers per set for sake of quick testing. All the scripts may take several hours to run on the full size datsets.

In [23]:
train_subfls = ['wav']#, 'T2', 'T3', 'T4', 'T5', 'T6', 'T7', 'T8', 'T9', 'T13']  #T13 used instead of T10 for gender balance
devel_subfls = []#, 'D2', 'D3', 'D4', 'D5', 'D6', 'D7', 'D8', 'D9', 'D10']
evalu_subfls = ['wav']#, 'E2', 'E3', 'E4', 'E5', 'E6','E7',  'E8', 'E9', 'E10']
train = pd.read_csv(LABEL_FOLDER + 'ASVspoof2019.LA.cm.train.trn.txt', sep=' ', header=None, names=['folder','file','default','method','source'])
train.sort_values(['folder', 'file'], inplace=True)
print(train)
devel = pd.read_csv(LABEL_FOLDER + 'ASVspoof2019.LA.cm.dev.trl.txt', sep=' ', header=None, names=['folder','file','default','method','source'])
devel.sort_values(['folder', 'file'], inplace=True)
#print(devel)
evalu = pd.read_csv(LABEL_FOLDER +'ASVspoof2019.LA.cm.eval.trl.txt', sep=' ', header=None, names=['folder','file','default','method','source'])
print(evalu)
evalu.sort_values(['folder', 'file'], inplace=True)

label_2_class = {'bonafide':1, 'spoof':0}

print('training samples:',len(train))
print('development samples:',len(devel))
print('evaluation samples:',len(evalu))

        folder          file default method    source
2580   LA_0079  LA_T_1004644       -    A01     spoof
13980  LA_0079  LA_T_1006715       -    A04     spoof
10180  LA_0079  LA_T_1007408       -    A03     spoof
10181  LA_0079  LA_T_1017386       -    A03     spoof
6380   LA_0079  LA_T_1025525       -    A02     spoof
...        ...           ...     ...    ...       ...
13979  LA_0098  LA_T_9962675       -    A03     spoof
25379  LA_0098  LA_T_9982036       -    A06     spoof
21579  LA_0098  LA_T_9983869       -    A05     spoof
17779  LA_0098  LA_T_9984124       -    A04     spoof
2579   LA_0098  LA_T_9987202       -      -  bonafide

[25380 rows x 5 columns]
        folder          file default method    source
0      LA_0039  LA_E_2834763       -    A11     spoof
1      LA_0014  LA_E_8877452       -    A14     spoof
2      LA_0040  LA_E_6828287       -    A16     spoof
3      LA_0022  LA_E_6977360       -    A09     spoof
4      LA_0031  LA_E_5932896       -    A13     spoof
..

## Speech Preprocessing and MFCC Extraction
Silence removal and MFCC feature extraction for training segments. More details about the bob.bio.spear involved libraries at:
https://www.idiap.ch/software/bob/docs/latest/bioidiap/bob.bio.spear/master/implemented.html

You can also skip this stage and load a set of feaures (see **Loading features** cell).

In [24]:
# Parameters
n_ceps = 84 # number of ceptral coefficients (implicit in extractor)
silence_removal_ratio = .1

In [25]:
subfolders = train_subfls
ground_truth = train

# initialize feature matrix
mfcc = []
mfcc_orig = []
mfcc_one = []
mfcc_two = []
mfcc_orig_one = []

y_list = []
#y = np.zeros((len(ground_truth),))
print("Extracting features for training stage.")

vad = preprocessor.Energy_Thr(ratio_threshold=silence_removal_ratio)
cepstrum = extractor.Cepstral()

k = 0
start_time = time.clock()

n_subfls = len(subfolders)
for folder in subfolders[0:n_subfls]:
    #print(folder, end=", ")
    train_folder = "".join([WAV_FOLDER,train_before,'/'])
    folder = "".join((train_folder,folder,'/'))
    print(folder)
    f_list = os.listdir(folder)
    # print(f_list)
    for f_name in f_list:
        if f_name.endswith(EXT):
        # ground truth
            try: 
                # 根据train中file(路径)字段，提取相应.wav文件的source(spoof or human)字段
                label = ground_truth[ground_truth.file==f_name[0:12]].source.values[0]
                #print(f_name[0:12], label)
            except IndexError:
                continue
            #y_list.append(label_2_class[label])
            # silence removal
            # print(vad)
            #rate,x = cqcc_ext.read(folder+f_name)
            #vad_data = cfcc_ext.vad(x)
            # CFCC extraction 
            #cqcc_feature = cqcc_ext.cqcc(vad_data,rate)
            #features.append(cqcc_feature)
            #k += 1
            
            
            
            y_list.append(label_2_class[label])
        # silence removal
        # print(f_name)
        # print(vad)
            x = cfcc_ext.read(folder+f_name)
            vad_data = vad(x)

            if vad_data:
                if not vad_data[2].max():
                    vad = preprocessor.Energy_Thr(ratio_threshold=silence_removal_ratio*.8)
                    vad_data = vad(x)
                    vad = preprocessor.Energy_Thr(ratio_threshold=silence_removal_ratio)
            # MFCC extraction 
                features = cepstrum(vad_data)
                print(features.shape)
                mfcc.append(features)
                mfcc_orig.append(features[:, :20])
                mfcc_one.append(features[:, 20:40])
                mfcc_two.append(features[:, 40:60])
                mfcc_orig_one.append(features[:, :40])
                print(features[:, :40].shape)
            else :
                print("err")
                mfcc.append(None)
                mfcc_orig.append(None)
                mfcc_one.append(None)
                mfcc_two.append(None)
                mfcc_orig_one.append(None)
            k += 1

# 这里是将人声与合成声进行了区分的，根据就是y
y = np.array(y_list)
Xf_mfcc = np.array(mfcc)
Xf_mfcc_orig = np.array(mfcc_orig)
Xf_mfcc_one = np.array(mfcc_one)
Xf_mfcc_two = np.array(mfcc_two)
Xf_mfcc_orig_one = np.array(mfcc_orig_one)
print(k,"files processed in",(time.clock()-start_time)/60,"minutes.")

Extracting features for training stage.
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_train/wav/


/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:19: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead


bob.bio.spear@2021-04-07 15:07:17,118 -- INFO: After thresholded Energy-based VAD there are 194 frames remaining over 194
(194, 60)
(194, 40)
bob.bio.spear@2021-04-07 15:07:17,297 -- INFO: After thresholded Energy-based VAD there are 255 frames remaining over 255
(255, 60)
(255, 40)
bob.bio.spear@2021-04-07 15:07:17,462 -- INFO: After thresholded Energy-based VAD there are 335 frames remaining over 335
(335, 60)
(335, 40)
bob.bio.spear@2021-04-07 15:07:17,719 -- INFO: After thresholded Energy-based VAD there are 524 frames remaining over 524
(524, 60)
(524, 40)
bob.bio.spear@2021-04-07 15:07:18,073 -- INFO: After thresholded Energy-based VAD there are 792 frames remaining over 792
(792, 60)
(792, 40)
bob.bio.spear@2021-04-07 15:07:18,539 -- INFO: After thresholded Energy-based VAD there are 265 frames remaining over 265
(265, 60)
(265, 40)
bob.bio.spear@2021-04-07 15:07:18,751 -- INFO: After thresholded Energy-based VAD there are 102 frames remaining over 502
(102, 60)
(102, 40)
bob.bi

(382, 60)
(382, 40)
bob.bio.spear@2021-04-07 15:07:30,701 -- INFO: After thresholded Energy-based VAD there are 325 frames remaining over 325
(325, 60)
(325, 40)
bob.bio.spear@2021-04-07 15:07:30,901 -- INFO: After thresholded Energy-based VAD there are 147 frames remaining over 339
(147, 60)
(147, 40)
bob.bio.spear@2021-04-07 15:07:31,006 -- INFO: After thresholded Energy-based VAD there are 314 frames remaining over 314
(314, 60)
(314, 40)
bob.bio.spear@2021-04-07 15:07:31,213 -- INFO: After thresholded Energy-based VAD there are 276 frames remaining over 276
(276, 60)
(276, 40)
bob.bio.spear@2021-04-07 15:07:31,400 -- INFO: After thresholded Energy-based VAD there are 208 frames remaining over 208
(208, 60)
(208, 40)
bob.bio.spear@2021-04-07 15:07:31,557 -- INFO: After thresholded Energy-based VAD there are 447 frames remaining over 447
(447, 60)
(447, 40)
bob.bio.spear@2021-04-07 15:07:31,831 -- INFO: After thresholded Energy-based VAD there are 311 frames remaining over 311
(311, 

(579, 60)
(579, 40)
bob.bio.spear@2021-04-07 15:07:47,584 -- INFO: After thresholded Energy-based VAD there are 74 frames remaining over 212
(74, 60)
(74, 40)
bob.bio.spear@2021-04-07 15:07:47,652 -- INFO: After thresholded Energy-based VAD there are 217 frames remaining over 217
(217, 60)
(217, 40)
bob.bio.spear@2021-04-07 15:07:47,843 -- INFO: After thresholded Energy-based VAD there are 139 frames remaining over 261
(139, 60)
(139, 40)
bob.bio.spear@2021-04-07 15:07:47,957 -- INFO: After thresholded Energy-based VAD there are 309 frames remaining over 309
(309, 60)
(309, 40)
bob.bio.spear@2021-04-07 15:07:48,214 -- INFO: After thresholded Energy-based VAD there are 336 frames remaining over 336
(336, 60)
(336, 40)
bob.bio.spear@2021-04-07 15:07:48,469 -- INFO: After thresholded Energy-based VAD there are 293 frames remaining over 293
(293, 60)
(293, 40)
bob.bio.spear@2021-04-07 15:07:48,673 -- INFO: After thresholded Energy-based VAD there are 331 frames remaining over 331
(331, 60)

...

(140, 60)
(140, 40)
bob.bio.spear@2021-04-07 16:49:57,937 -- INFO: After thresholded Energy-based VAD there are 479 frames remaining over 479
(479, 60)
(479, 40)
bob.bio.spear@2021-04-07 16:49:58,222 -- INFO: After thresholded Energy-based VAD there are 433 frames remaining over 433
(433, 60)
(433, 40)
bob.bio.spear@2021-04-07 16:49:58,497 -- INFO: After thresholded Energy-based VAD there are 282 frames remaining over 282
(282, 60)
(282, 40)
bob.bio.spear@2021-04-07 16:49:58,666 -- INFO: After thresholded Energy-based VAD there are 426 frames remaining over 426
(426, 60)
(426, 40)
bob.bio.spear@2021-04-07 16:49:58,911 -- INFO: After thresholded Energy-based VAD there are 462 frames remaining over 462
(462, 60)
(462, 40)
bob.bio.spear@2021-04-07 16:49:59,186 -- INFO: After thresholded Energy-based VAD there are 292 frames remaining over 292
(292, 60)
(292, 40)
bob.bio.spear@2021-04-07 16:49:59,361 -- INFO: After thresholded Energy-based VAD there are 204 frames remaining over 204
(204, 

(463, 60)
(463, 40)
bob.bio.spear@2021-04-07 16:50:10,137 -- INFO: After thresholded Energy-based VAD there are 144 frames remaining over 144
(144, 60)
(144, 40)
bob.bio.spear@2021-04-07 16:50:10,239 -- INFO: After thresholded Energy-based VAD there are 339 frames remaining over 339
(339, 60)
(339, 40)
bob.bio.spear@2021-04-07 16:50:10,451 -- INFO: After thresholded Energy-based VAD there are 255 frames remaining over 255
(255, 60)
(255, 40)
bob.bio.spear@2021-04-07 16:50:10,614 -- INFO: After thresholded Energy-based VAD there are 633 frames remaining over 633
(633, 60)
(633, 40)
bob.bio.spear@2021-04-07 16:50:10,989 -- INFO: After thresholded Energy-based VAD there are 294 frames remaining over 294
(294, 60)
(294, 40)
bob.bio.spear@2021-04-07 16:50:11,178 -- INFO: After thresholded Energy-based VAD there are 173 frames remaining over 173
(173, 60)
(173, 40)
bob.bio.spear@2021-04-07 16:50:11,293 -- INFO: After thresholded Energy-based VAD there are 357 frames remaining over 357
(357, 

(336, 60)
(336, 40)
bob.bio.spear@2021-04-07 16:50:22,690 -- INFO: After thresholded Energy-based VAD there are 258 frames remaining over 258
(258, 60)
(258, 40)
bob.bio.spear@2021-04-07 16:50:22,864 -- INFO: After thresholded Energy-based VAD there are 213 frames remaining over 540
(213, 60)
(213, 40)
bob.bio.spear@2021-04-07 16:50:23,010 -- INFO: After thresholded Energy-based VAD there are 492 frames remaining over 492
(492, 60)
(492, 40)
bob.bio.spear@2021-04-07 16:50:23,299 -- INFO: After thresholded Energy-based VAD there are 261 frames remaining over 261
(261, 60)
(261, 40)
bob.bio.spear@2021-04-07 16:50:23,480 -- INFO: After thresholded Energy-based VAD there are 141 frames remaining over 141
(141, 60)
(141, 40)
bob.bio.spear@2021-04-07 16:50:23,568 -- INFO: After thresholded Energy-based VAD there are 282 frames remaining over 282
(282, 60)
(282, 40)
bob.bio.spear@2021-04-07 16:50:23,746 -- INFO: After thresholded Energy-based VAD there are 185 frames remaining over 185
(185, 

(207, 60)
(207, 40)
bob.bio.spear@2021-04-07 16:50:34,217 -- INFO: After thresholded Energy-based VAD there are 196 frames remaining over 196
(196, 60)
(196, 40)
bob.bio.spear@2021-04-07 16:50:34,341 -- INFO: After thresholded Energy-based VAD there are 190 frames remaining over 190
(190, 60)
(190, 40)
bob.bio.spear@2021-04-07 16:50:34,470 -- INFO: After thresholded Energy-based VAD there are 329 frames remaining over 329
(329, 60)
(329, 40)
bob.bio.spear@2021-04-07 16:50:34,673 -- INFO: After thresholded Energy-based VAD there are 348 frames remaining over 348
(348, 60)
(348, 40)
bob.bio.spear@2021-04-07 16:50:34,882 -- INFO: After thresholded Energy-based VAD there are 243 frames remaining over 243
(243, 60)
(243, 40)
bob.bio.spear@2021-04-07 16:50:35,039 -- INFO: After thresholded Energy-based VAD there are 331 frames remaining over 331
(331, 60)
(331, 40)
bob.bio.spear@2021-04-07 16:50:35,244 -- INFO: After thresholded Energy-based VAD there are 399 frames remaining over 399
(399, 

/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:87: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead


In [27]:
print(Xf_mfcc[y==0].shape)

(22800,)


In [69]:
np.vstack(Xf[y==1]).shape

(34771, 84)

In [80]:
ground_truth

folder      file default    method    source  z  z_gmm  score_gmm
107206     E2  E200001s       -     spoof     spoof  0    1.0   7.622108
98412      E2  E200002s       -     spoof     spoof  0    1.0  10.544859
102443     E2  E200003h       -  bonafide  bonafide  1    0.0  -2.888099
103712     E2  E200004s       -     spoof     spoof  0    0.0  -2.797664
98984      E2  E200005h       -  bonafide  bonafide  1    1.0  17.829845
...       ...       ...     ...       ...       ... ..    ...        ...
105581     E2  E208996h       -  bonafide  bonafide  1    0.0  -3.521843
100661     E2  E208997h       -  bonafide  bonafide  1    0.0  -3.759985
106825     E2  E208998s       -     spoof     spoof  0    1.0   6.707735
102766     E2  E208999h       -  bonafide  bonafide  1    1.0   7.150391
105172     E2  E209000h       -  bonafide  bonafide  1    0.0  -2.000744

[9000 rows x 8 columns]

### Saving features

In [26]:
np.save('Xf_mfcc.npy',Xf_mfcc)
np.save('Xf_mfcc_orig.npy',Xf_mfcc_orig)
np.save('Xf_mfcc_one.npy',Xf_mfcc_one)
np.save('Xf_mfcc_two.npy',Xf_mfcc_two)
np.save('Xf_mfcc_orig_one.npy',Xf_mfcc_orig_one)
np.save('y_mfcc.npy',y)
print('Feature and label matrices saved to disk')

Feature and label matrices saved to disk


### Loading features

In [136]:
# Load already extracter features to skip the preprocessing-extraction stage
# Xf = np.load('train_features_10.npy')
# y = np.load('y_10.npy')
Xf = np.load('X9.npy',allow_pickle=True)
y = np.load('y9.npy',allow_pickle=True)

In [227]:
print(Xf.shape)

(1200,)


# GMM - ML Classification

## GMM Training
Train the GMMs for natural and synthetic speach. For documentation on bob.bio k-means and GMM machines see:
https://pythonhosted.org/bob.learn.em/guide.html

You can also skip the training stage and load an already trained GMM model (see cell **Loading GMM Model**).

In [9]:
# Parameters of the GMM machines
n_gaussians = 512 # number of Gaussians
max_iterats = 25 # maximum number of iterations

### GMM for natural speech 

In [7]:
# Initialize and train k-means machine: the means will initialize EM algorithm for GMM machine
start_time = time.clock()
kmeans_nat = em.KMeansMachine(n_gaussians,n_ceps)
kmeansTrainer = em.KMeansTrainer()
print(kmeans_nat.shape,Xf[y==1].shape)
em.train(kmeansTrainer, kmeans_nat, np.vstack(Xf[y==1]), max_iterations = max_iterats, convergence_threshold = 1e-5)
#kmeans_nat.means

# initialize and train GMM machine
gmm_nat = em.GMMMachine(n_gaussians,n_ceps)
trainer = em.ML_GMMTrainer(True, True, True)
gmm_nat.means = kmeans_nat.means
em.train(trainer, gmm_nat, np.vstack(Xf[y==1]), max_iterations = max_iterats, convergence_threshold = 1e-5)
#gmm_nat.save(HDF5File('gmm_nat.hdf5', 'w'))
print("Done in:", (time.clock() - start_time)/60, "minutes")
print(gmm_nat)

/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:2: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  


(1024, 84) (63007,)
Done in: 136.19362388333332 minutes


/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:15: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  from ipykernel import kernelapp as app


### GMM for synthetic speech

In [10]:
# initialize and train k-means machine: the means will initialize EM algorithm for GMM machine
start_time = time.clock()
kmeans_synt = em.KMeansMachine(n_gaussians,n_ceps)
kmeansTrainer = em.KMeansTrainer()
print(kmeans_synt.shape,Xf[y==0].shape)
em.train(kmeansTrainer, kmeans_synt, np.vstack(Xf[y==0]), max_iterations = max_iterats, convergence_threshold = 1e-5)

# initialize and train GMM machine
gmm_synt = em.GMMMachine(n_gaussians,n_ceps)
trainer = em.ML_GMMTrainer(True, True, True)
gmm_synt.means = kmeans_synt.means
em.train(trainer, gmm_synt, np.vstack(Xf[y==0]), max_iterations = max_iterats, convergence_threshold = 1e-5)
print("Done in:", (time.clock() - start_time)/60, "minutes")
#gmm_synt.save(HDF5File('gmm_synt.hdf5', 'w'))
print(gmm_synt)

/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:2: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  


(1024, 84) (87151,)
Done in: 159.00801165 minutes


/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:13: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  del sys.path[0]


### Saving GMM model

In [52]:
gmm_nat.save(HDF5File('gmm_nat_500seg.hdf5', 'w'))
gmm_synt.save(HDF5File('gmm_synt_500seg.hdf5', 'w'))

### Loading GMM model

In [55]:
gmm_nat = em.GMMMachine()
gmm_nat.load(HDF5File('gmm_nat_500seg.hdf5', 'r'))
gmm_synt = em.GMMMachine()
gmm_synt.load(HDF5File('gmm_synt_500seg.hdf5','r'))

In [ ]:
np.save('p_gmm_ml_eval_10.npy',llr_score)
np.save('z_gmm_ml_eval_est_10.npy',z_gmm)

## GMM-ML Scoring
Extract the features for the testing data, compute the likelihood ratio test and  compute ROC AUC and estimated EER scores.

In [11]:
status = 'evalu' # 'devel'(= test) OR 'evalu'(= hold out)
start_time = time.clock()
F_FILE = np.array([])

if status == 'devel':
    subfolders = devel_subfls
    ground_truth = devel
elif status == 'evalu':
    subfolders = evalu_subfls
    ground_truth = evalu
n_subfls = len(subfolders)
# initialize score and class arrays
llr_gmm_score = np.zeros(len(ground_truth),)
z_gmm = np.zeros(len(ground_truth),)
print(status)

vad = preprocessor.Energy_Thr(ratio_threshold=.1)
cepstrum = extractor.Cepstral()

k = 0
thr = .5

#speaker = ground_truth[ground_truth.folder==speaker_id]
f_list = list(ground_truth.file)
evalu_folder = "".join([WAV_FOLDER,evalu_before,'/'])
folder = "".join([evalu_folder,evalu_subfls[0],'/'])
#print(f_list)
#print(folder)
for f in f_list:
    if isinstance(f,str):
        f_name = "".join([folder,f,EXT])
    if os.path.exists(f_name):
        rate,x = cqcc_ext.read(f_name)
        # voice activity detection
        vad_data = cfcc_ext.vad(x)
        
        # CFCC extraction 
        cqcc_feature = cqcc_ext.cqcc(vad_data,rate)
        # Log likelihood ratio computation
        llr_gmm_score[k] = gmm_nat(cqcc_feature)-gmm_synt(cqcc_feature)
        z_gmm[k] = int(llr_gmm_score[k]>0)
         
        #class_2_label={0:'spoof',1:'bonafide'}
        #if label_2_class[ground_truth.iloc[k].source] != z_gmm[k]:
        #    F_FILE = np.append(F_FILE,ground_truth.iloc[k].file)
            
    k += 1
        
ground_truth['z'] = ground_truth.source.map(lambda x: int(x=='bonafide'))
ground_truth['z_gmm'] = z_gmm
ground_truth['score_gmm'] = llr_gmm_score
#print(roc_auc_score(ground_truth.z, ground_truth.z_gmm))
print(k,"files processed in",(time.clock()-start_time)/60,"minutes.")

/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:2: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  


evalu
57382 files processed in 1370.784710266667 minutes.


/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:53: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead


In [11]:
F_FILE

array(['EHUM10001', 'EHUM10003', 'EHUM10004', 'EHUM10005', 'EHUM10006',
       'EHUM10008', 'EHUM10009', 'EHUM10010', 'EHUM10012', 'EHUM10013',
       'EHUM10016', 'EHUM10017', 'EHUM10022', 'EHUM10023', 'EHUM10024',
       'EHUM10025', 'EHUM10026', 'EHUM10027', 'EHUM10028', 'EHUM10029',
       'EHUM10030', 'EHUM10031', 'EHUM10032', 'EHUM10033', 'EHUM10034',
       'EHUM10035', 'EHUM10036', 'EHUM10037', 'EHUM10038', 'EHUM10039',
       'EHUM10040', 'EHUM10041', 'EHUM10042', 'EHUM10043', 'EHUM10044',
       'EHUM10045', 'EHUM10046', 'EHUM10047', 'EHUM10048', 'EHUM10049',
       'EHUM10050', 'EHUM10051', 'EHUM10052', 'EHUM10053', 'EHUM10054',
       'EHUM10055', 'EHUM10057', 'EHUM10058', 'EHUM10059', 'EHUM10060',
       'EHUM10061', 'EHUM10062', 'EHUM10063', 'EHUM10064', 'EHUM10065',
       'EHUM10066', 'EHUM10067', 'EHUM10069', 'EHUM10070', 'EHUM10071',
       'EHUM10072', 'EHUM10073', 'EHUM10074', 'EHUM10075', 'EHUM10078',
       'EHUM10080', 'EHUM10082', 'EHUM10083', 'EHUM10084', 'EHUM

In [12]:
# Performance evaluation

#实际humans个数
humans = sum(ground_truth.z==1)
print("实际humans个数:", humans)

#实际spoofed个数
spoofed = sum(ground_truth.z==0)
print("实际spoofed个数:", spoofed)

#预测humans个数
pre_humans = sum(ground_truth.z_gmm==1)
print("预测humans个数:", pre_humans)

#预测spoofed个数
pre_spoofed = sum(ground_truth.z_gmm==0)
print("预测spoofed个数:", pre_spoofed)

tp = 0
tn = 0
fp = 0
fn = 0
for i in ground_truth.index:
    if ground_truth.z[i] == 1 and ground_truth.z_gmm[i]==1:
        tp = tp + 1
    elif ground_truth.z[i] == 1 and ground_truth.z_gmm[i]==0:
        fn = fn + 1
    elif ground_truth.z[i] == 0 and ground_truth.z_gmm[i]==0:
        tn = tn + 1
    elif ground_truth.z[i] == 0 and ground_truth.z_gmm[i]==1:
        fp = fp + 1
print("TP_Num:", tp)
print("TN_Num:", tn)
print("FP_Num:", fp)
print("FN_Num:", fn)

tpr = tp/(tp+fn)
fpr = fp/(fp+tn)
tnr = tn/(fp+tn)
fnr = fn/(tp+fn)
acc = (tp+tn)/(tp+fp+tn+fn)
eer = (fpr*fnr)/(fpr+fnr)
print("TPR:", tpr)
print("FPR:", fpr)
print("TNR:", tnr)
print("FNR:", fnr)
print("ROC:", roc_auc_score(ground_truth.z, ground_truth.z_gmm))
print("Accuracy:", acc)
print("EER:", eer)

# humans = z_gmm[z_dvl==0]
# spoofed = z_gmm[z_dvl==1]
# fnr = 100*(1-(humans<thr).sum()/len(humans))
# fpr = 100*(1-(spoofed>=thr).sum()/len(spoofed))
# print("ROC AUC score:", roc_auc_score(z_dvl,z_gmm))
# print("False negative rate %:", fnr)
# print("False positive rate %:", fpr)
# print("EER %: <=", (fnr+fpr)/2)

实际humans个数: 0
实际spoofed个数: 57382
预测humans个数: 19875
预测spoofed个数: 37507
TP_Num: 0
TN_Num: 37507
FP_Num: 19875
FN_Num: 0


ZeroDivisionError: division by zero

In [62]:
method = {}
for index, row in ground_truth.iterrows():
    if row['z'] != row['z_gmm']:
        if row['method'] in method:
            method[row['method']] = method[row['method']] + 1
        else:
            method[row['method']] = 1
print(method)

{'-': 6757, 'A07': 17, 'A16': 18, 'A10': 28, 'A12': 21, 'A11': 25, 'A13': 6, 'A15': 4, 'A18': 13, 'A17': 14, 'A19': 39, 'A08': 2}


In [47]:
ground_truth

folder        file method source  z  z_gmm  score_gmm
2597     D1  D1_1002598  human  human  1    1.0   1.447147
2598     D1  D1_1002599  human  human  1    1.0   2.336380
2599     D1  D1_1002600  human  human  1    1.0   3.082637
2600     D1  D1_1002601  human  human  1    1.0   3.716948
2601     D1  D1_1002602  human  human  1    1.0   0.914256
...     ...         ...    ...    ... ..    ...        ...
7767     D3  D3_1007768     S1  spoof  0    0.0  -2.641017
7768     D3  D3_1007769     S2  spoof  0    0.0  -0.571958
7769     D3  D3_1007770     S3  spoof  0    0.0  -5.441518
7770     D3  D3_1007771     S4  spoof  0    0.0  -4.762759
7771     D3  D3_1007772     S5  spoof  0    0.0  -1.451432

[3050 rows x 7 columns]

### EER computation

Adjust the threshold $thr$ to reduce $FNR-FPR$ for a more accurate estimate of the $EER$.

The Equal Error Rate ($EER$) is the value where the false negative rate ($FNR$) equals the false positive rate ($FPR$). It's an error metric commonly used to characterize biometric systems.

In [47]:
thr = -.115
pz = llr_gmm_score
spoofed = pz[np.array(ground_truth.z)==1]
humans = pz[np.array(ground_truth.z)==0]
fnr = 100*(humans>thr).sum()/len(humans)
fpr = 100*(spoofed<=thr).sum()/len(spoofed)
print("False negative vs positive rates %:", fnr, fpr)
print("FNR - FPR %:", fnr-fpr)
if np.abs(fnr-fpr) <.25:
    print("EER =", (fnr+fpr)/2,"%")
else:
    print("EER ~", (fnr+fpr)/2,"%")

False negative vs positive rates %: 0.3345997002544352 99.53318745441284
FNR - FPR %: -99.19858775415841
EER ~ 49.933893577333635 %
